In [1]:
import json
import re

def load_data(filename):
    with open(filename, 'r', encoding='utf-8') as f:
        return json.load(f)

def extract_numbers(call_no):
    # Extract numbers from the call number, handle ranges as well
    if '-' in call_no:
        start, end = call_no.split('-')
        return float(start), float(end)
    match = re.match(r"(\d+\.\d+)", call_no)
    if match:
        return float(match.group(1)), float(match.group(1))
    return None, None

def find_nearest_call_no(data, input_call_no):
    nearest_book = None
    nearest_distance = float('inf')
    nearest_ke_sach = None
    input_number = input_call_no
    
    for shelf in data["library"]["Dãy sách"]:
        for ke_sach in shelf["kệ sách"]:
            for book in ke_sach["books"]:
                start_number, end_number = extract_numbers(book["call_no"])
                if start_number is not None:
                    # Compare with the start and end numbers if it's a range
                    if end_number is not None:
                        distance_start = abs(start_number - input_number)
                        distance_end = abs(end_number - input_number)
                        distance = min(distance_start, distance_end)
                    else:
                        distance = abs(start_number - input_number)
                    
                    if distance < nearest_distance:
                        nearest_distance = distance
                        nearest_book = book
                        nearest_ke_sach = ke_sach["kệ sách"]
    
    return nearest_book, nearest_ke_sach

In [2]:
def preprocess_call_no(call_no):
    parts = call_no.split()
    print(parts)
    floats = []
    for part in parts:
        try:
            num = float(part)
            if (num < 1000)and (num>0):
                floats.append(num)
            else:
                continue
        except ValueError:
            continue
    return floats

In [3]:
print(preprocess_call_no('537z.6 T877'))

['537z.6', 'T877']
[]


In [4]:
import random
book_infos_data = load_data('./Knowledge/Books/Json/sample2.json')
data = load_data('./book_shelf.json')
def process_book_infos(library_data, book_infos_data):
    for book_info in book_infos_data["book_infos"]:
        print("inthe process of book info: ",book_info)
        call_no = book_info.get("Call no")
        if call_no is not None:
            call_no = preprocess_call_no(call_no)
        else :
            pos = random.randint(401, 414)
            book_info["vị trí"] = "Kệ số "+ str(pos)
            continue
        if call_no == None:
            pos = random.randint(401, 414)
            book_info["vị trí"] = "Kệ số "+ str(pos)
            continue 
        if len(call_no)==1: 
            pos = random.randint(401, 414)
            book_info["vị trí"] = "Kệ số "+ str(pos)
            call_no = call_no[0]
        elif len(call_no)>=2 :
            pos = random.randint(401, 414)
            book_info["vị trí"] = "Kệ số "+ str(pos)
            print ("need to check")
            print(call_no)
            call_no = call_no[0]
        elif len(call_no) == 0:
            pos = random.randint(401, 414)
            book_info["vị trí"] = "Kệ số "+ str(pos)
            continue 
        print("call no:", call_no)
        if call_no :
            nearest_book, nearest_ke_sach = find_nearest_call_no(library_data, call_no)
            if nearest_book:
                print(f"Book Info Call no: {call_no}")
                print(f"Nearest Library Call no: {nearest_book['call_no']}")
                print(f"Nearest Book Title: {nearest_book['tên sách']}")
                print(f"Located at Kệ sách: {nearest_ke_sach}")
                book_info["vị trí"] = "Kệ số "+ str(nearest_ke_sach)
                print()
            else:
                print(f"Book Info Call no: {call_no} has no matching call number found.")
                print()
        else:
            print(f"Book Info Call no: {call_no} is invalid or missing.")
            print()
    with open('updated_book_sample.json', 'w', encoding='utf-8') as f:
        json.dump(book_infos_data, f, ensure_ascii=False, indent=4)

In [5]:
process_book_infos(data,book_infos_data)

inthe process of book info:  {'Tác giả': 'Dương Thị Vân (ch.b), Hoàng Thị Thục, Âu Thị Cẩm Linh', 'Nhà xuất bản': 'Đại học Quốc Gia Thành phố Hồ Chí Minh', 'Năm xuất bản': '2020', 'Call no': '027 D928-V217', 'Tên sách': 'Giáo trình marketing thông tin thư viện', 'Loại sách': 'UTE. Thông tin -Thư viện', 'ID': 1, 'Keyword': ['Từ khóa: Giáo trình, Thông tin thư viện, Truyền thông'], 'Mô tả': 'Giáo trình marketing thông tin thư viện/ Dương Thị Vân (ch.b), Hoàng Thị Thục, Âu Thị Cẩm Linh. -- TP. Hồ Chí Minh.: Đại học Quốc gia Thành phố Hồ Chí Minh, 2020. - 24tr.; 24cm.\nISBN 9786047379927\nCall no. : 027 D928-V217', 'Nội dung đầu sách': '/Knowledge/Books/PDF/UTE. Thông tin -Thư viện/skd002890_9887.pdf'}
['027', 'D928-V217']
call no: 27.0
Book Info Call no: 27.0
Nearest Library Call no: 005.13-005.133
Nearest Book Title: LẬP TRÌNH WEB VÕI ASP.NET - GT MICROSOFT VISUAL BASIC, LẬP TRÌNH CƠ SỞ DỮ LIỆU 60
Located at Kệ sách: 101

inthe process of book info:  {'Tác giả': 'None', 'Nhà xuất bản': '

In [2]:
book_infos_data = load_data('./updated_book_sample.json')

In [3]:
def modify_book_info(book_info):
    # Reorder keys and remove "Call no"
    modified_info = {
        "Tên sách": book_info["Tên sách"],
        "Loại sách": book_info["Loại sách"],
        "ID": book_info["ID"],
        "Tác giả": book_info["Tác giả"],
        "Nhà xuất bản": book_info["Nhà xuất bản"],
        "Năm xuất bản": book_info["Năm xuất bản"],
        "Keyword": book_info["Keyword"],
        "Mô tả": book_info["Mô tả"].replace("\nCall no. : 027 D928-V217", ""),
        "vị trí": book_info["vị trí"],
        "Nội dung đầu sách": book_info["Nội dung đầu sách"]
    }
    return modified_info

# Modify the book information
book_infos_data["book_infos"] = [modify_book_info(book) for book in book_infos_data["book_infos"]]

# Save the modified JSON object to an output file
output_filename = 'modified_book_infos.json'
with open(output_filename, 'w', encoding='utf-8') as output_file:
    json.dump(book_infos_data, output_file, ensure_ascii=False, indent=4)

print(f'Modified JSON object has been saved to {output_filename}')

Modified JSON object has been saved to modified_book_infos.json
